In [1]:
import AFQ.data.fetch as afd
from AFQ.api.group import GroupAFQ
from dipy.io.streamline import load_tractogram

from AFQ.api.bundle_dict import BundleDict
import os.path as op
import nibabel as nib
import numpy as np

/Users/john/miniconda3/envs/afq/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
afd.organize_stanford_data()
stanford_hardi_path = op.join(op.expanduser('~'), 'AFQ_data', 'stanford_hardi_vof')  # ~/AFQ_data/stanford_hardi

INFO:AFQ:fetching Stanford HARDI data
INFO:AFQ:Dataset is already in place. If you want to fetch it again please first remove the folder /Users/john/AFQ_data/stanford_hardi/derivatives


In [3]:
def roi_from_atlas(label_list, template="AICHA.nii"):
    if isinstance(label_list, dict):
        unfolded_label_list = []
        for labels in label_list.values():
            unfolded_label_list.extend(list(labels))
        label_list = unfolded_label_list

    atlas_img = nib.load(template)
    atlas_data = atlas_img.get_fdata()
    if len(atlas_data.shape) > 3:
        atlas_data = atlas_data[..., 0]
    this_roi = np.zeros(atlas_data.shape[:3])
    for label in label_list:
        this_roi = np.logical_or(atlas_data==label, this_roi)
    return nib.Nifti1Image(this_roi.astype(np.float32), atlas_img.affine)


In [4]:
relevant_labels_aal = {
    "L": {
        "Ventral": {
            "Occipital Inf": [53],
            "Lingual": [47],
            "Fusiform": [55],
            "Temporal inferior": [89]
        },
        "Dorsal": {
            "Occipital Sup": [49],
            "Parietal lobe": [59, 61, 63, 65],
            "Occipital Mid": [51],
        }
    }, "R": {
        "Ventral": {
            "Occipital Inf": [54],
            "Lingual": [48],
            "Fusiform": [56],
            "Temporal inferior": [90]
        },
        "Dorsal": {
            "Occipital Sup": [50],
            "Parietal lobe": [60, 62, 64, 66],
            "Occipital Mid": [52],
        }
    }
}

In [13]:
AAL = "MNI_AAL_AndMore.nii.gz"
my_bundle_dict_aal = {
    "L_pArc": {
        "start": roi_from_atlas(relevant_labels_aal["L"]["Dorsal"]["Parietal lobe"], template=AAL),
        "include": [afd.read_templates()["SLFt_roi2_L"]],
        "exclude": [afd.read_templates()["SLF_roi1_L"]],
        "primary_axis": 2, "primary_axis_percentage": 50},
    "R_pArc": {
        "start": roi_from_atlas(relevant_labels_aal["R"]["Dorsal"]["Parietal lobe"], template=AAL),
        "include": [afd.read_templates()["SLFt_roi2_R"]],
        "exclude": [afd.read_templates()["SLF_roi1_R"]],
        "primary_axis": 2, "primary_axis_percentage": 50},
    "L_vertical": {
        "end": roi_from_atlas(relevant_labels_aal["L"]["Ventral"], template=AAL),
        "start": roi_from_atlas(relevant_labels_aal["L"]["Dorsal"], template=AAL),
        "primary_axis": 2, "primary_axis_percentage": 50},
    "R_vertical": {
        "end": roi_from_atlas(relevant_labels_aal["R"]["Ventral"], template=AAL),
        "start": roi_from_atlas(relevant_labels_aal["R"]["Dorsal"], template=AAL),
        "primary_axis": 2, "primary_axis_percentage": 50}
}

DEBUG:AFQ:loading AFQ templates
DEBUG:AFQ:AFQ templates loaded in 0.0550 seconds
DEBUG:AFQ:loading AFQ templates
DEBUG:AFQ:AFQ templates loaded in 0.0383 seconds
DEBUG:AFQ:loading AFQ templates
DEBUG:AFQ:AFQ templates loaded in 0.0412 seconds
DEBUG:AFQ:loading AFQ templates
DEBUG:AFQ:AFQ templates loaded in 0.0368 seconds


In [14]:
import logging
logger = logging.getLogger('AFQ')
logger.setLevel(logging.DEBUG)

In [18]:
from AFQ.definitions.image import RoiImage
from AFQ.api.bundle_dict import BundleDict


myafq = GroupAFQ(
    stanford_hardi_path,
    bundle_info=BundleDict(["ARC_L", "ARC_R"]) + BundleDict(my_bundle_dict_aal),
    preproc_pipeline='vistasoft',
    tracking_params={
        "n_seeds": 50000,
        "random_seeds": True,
        "seed_mask": RoiImage(use_waypoints=True, use_endpoints=True),
        "min_length": 20
    },
    clean_params={"distance_threshold": 3, "length_threshold": 5, "clean_rounds": 20},
    segmentation_params={"save_intermediates": "inters"}
    )
myafq.clobber(dependent_on="recog")

DEBUG:AFQ:loading AFQ templates
DEBUG:AFQ:AFQ templates loaded in 0.0006 seconds
DEBUG:AFQ:loading callosum templates
DEBUG:AFQ:callosum templates loaded in 0.0004 seconds
/Users/john/miniconda3/envs/afq/lib/python3.9/site-packages/bids/layout/validation.py:151: UserWarning:

The PipelineDescription field was superseded by GeneratedBy in BIDS 1.4.0. You can use ``pybids upgrade`` to update your derivative dataset.



In [19]:
myafq.export("all_bundles_figure")["01"][0]

INFO:AFQ:Preparing Segmentation Parameters
INFO:AFQ:Preprocessing Streamlines
INFO:AFQ:Assigning Streamlines to Bundles
INFO:AFQ:Finding Streamlines for ARC_L
INFO:AFQ:9836 streamlines exceed the probability threshold.
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 7260/7260 [00:02<00:00, 2431.32it/s]
INFO:AFQ:405 streamlines selected with waypoint ROIs
INFO:AFQ:Filtering by endpoints
INFO:AFQ:Before filtering 405 streamlines
INFO:AFQ:After filtering by endpoints, 196 streamlines
INFO:AFQ:Finding Streamlines for ARC_R
INFO:AFQ:8170 streamlines exceed the probability threshold.
100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 6750/6750 [00:00<00:00, 40525.43it/s]
INFO:AFQ:558 streamlin

DEBUG:AFQ:Rounds elapsed: 0, num removed: 40
DEBUG:AFQ:Removed indicies: [  9  10  11  18  22  23  25  31  32  42  45  49  53  60  74  91  92  94
  96  97 101 103 104 106 107 114 116 118 120 123 126 142 146 147 153 156
 161 176 182 186]
DEBUG:AFQ:Shape of fgarray: (156, 100, 3)
DEBUG:AFQ:Shape of m_dist: (156, 100)
DEBUG:AFQ:Maximum m_dist: 3.668959090729929
DEBUG:AFQ:Maximum m_dist for each fiber: [3.16267321 1.94194928 2.35123503 1.1970064  3.62003874 1.9085889
 3.31727562 2.26912873 2.92071948 1.99386375 2.82613638 3.15195255
 1.77080361 1.10701357 1.80727428 2.26790022 3.4199143  3.49866217
 1.03676295 2.11833884 1.76397174 2.26972852 2.08052958 2.58574012
 2.26754462 1.19357301 2.56391511 2.75597467 1.96755468 3.24337066
 1.8147362  2.41646144 1.46540929 3.10791647 2.51218533 1.11250156
 3.04578977 2.86642053 1.85452359 1.24401909 2.29003098 1.73958
 1.68449195 1.39994767 1.46214893 1.77476394 3.21720257 1.79939782
 1.14948228 0.94725591 3.06458526 0.89148029 2.00525015 2.80917153

DEBUG:AFQ:Shape of length_z: (108,)
DEBUG:AFQ:Maximum length_z: 2.6980491323200986
DEBUG:AFQ:length_z for each fiber: [-0.46609931 -0.66745421 -1.01263404  1.5474497  -1.24275392 -0.63868922
  1.5474497  -0.03462452 -0.92633908  0.36808528  1.25979984 -1.55916877
  1.20226987  0.65573514  0.88585503 -1.04139902 -0.46609931  1.02967996
 -0.12091948  1.60497967 -0.17844945 -1.67422871 -0.98386905  2.69804913
 -0.60992424 -0.37980435 -0.84004412  0.943385   -0.09215449 -0.46609931
 -0.32227438 -0.49486429 -0.29350939 -1.15645897 -0.37980435 -1.12769398
 -0.95510407  1.02967996  1.60497967 -1.44410882  0.19549537  0.36808528
 -0.66745421 -0.09215449  0.22426035  0.97214998 -0.20721443  0.13796539
  1.20226987  0.82832505 -0.69621919  0.28179032 -0.49486429  1.86386454
 -0.29350939 -0.20721443 -0.14968446 -0.06338951 -2.47964831 -0.58115925
 -0.52362928  1.72003961 -0.12091948  0.13796539  1.60497967 -2.65223823
 -1.01263404  0.79956007  0.05167044 -0.92633908 -0.89757409  1.05844494
  0.88

DEBUG:AFQ:Rounds elapsed: 6, num removed: 5
DEBUG:AFQ:Removed indicies: [ 8 24 30 57 60]
DEBUG:AFQ:Shape of fgarray: (72, 100, 3)
DEBUG:AFQ:Shape of m_dist: (72, 100)
DEBUG:AFQ:Maximum m_dist: 3.28329203831003
DEBUG:AFQ:Maximum m_dist for each fiber: [2.90385966 2.3613641  2.43919735 2.84291136 2.5951696  2.11187431
 2.40036107 1.52596144 2.87773419 2.71912535 1.58586882 2.89125914
 2.5069686  2.36646913 2.49770658 1.06073837 1.81314284 2.83594757
 2.61174033 1.86722661 1.30260586 2.64128503 2.7893958  1.17087673
 1.3168577  1.07168592 2.51375467 3.28329204 2.56931328 2.58097516
 2.65923579 1.90882701 1.86478096 1.93335364 0.96667831 1.61084593
 1.59674446 1.47447775 2.30101548 1.43277523 2.35278566 2.60053269
 2.66668548 3.02734882 2.0965186  1.88532067 2.9386085  2.8466876
 2.45712168 2.78853264 2.61865278 1.99175924 1.3097421  2.34707779
 1.96328942 2.70268859 1.89678571 1.92193577 2.4846333  1.31189519
 3.12467764 1.96319207 1.88878726 1.33998401 3.23153298 2.35855751
 3.20995717 2

DEBUG:AFQ:Shape of length_z: (51,)
DEBUG:AFQ:Maximum length_z: 2.312118510805633
DEBUG:AFQ:length_z for each fiber: [-0.94974291 -0.84452157  0.73379847 -1.61614471  1.36512649 -0.98481669
  0.13754423  2.24197095  0.06739667 -0.45871001 -0.73930024  1.43527404
 -0.28334111 -0.10797222 -0.07289844 -0.17811978 -1.09003802 -0.87959535
  1.54049538 -0.52885757  0.45320824  1.29497893 -0.56393134 -0.31841489
 -0.07289844  0.03232289  0.10247045  0.20769179 -0.42363623 -0.35348867
  2.24197095 -0.84452157 -0.8094478  -0.59900512  1.85615939  1.22483137
 -0.17811978  1.22483137 -0.45871001 -1.54599715  1.18975759 -0.94974291
 -0.84452157 -0.91466913  0.13754423 -0.31841489  0.17261801 -1.68629226
 -0.07289844 -0.28334111  2.31211851]
DEBUG:AFQ:Rounds elapsed: 11, num removed: 7
DEBUG:AFQ:Removed indicies: [ 4  5  7 11 20 43 50]
DEBUG:AFQ:Shape of fgarray: (44, 100, 3)
DEBUG:AFQ:Shape of m_dist: (44, 100)
DEBUG:AFQ:Maximum m_dist: 3.541206340519512
DEBUG:AFQ:Maximum m_dist for each fiber: [2.

...

DEBUG:AFQ:Shape of length_z: (63,)
DEBUG:AFQ:Maximum length_z: 2.665550752065601
DEBUG:AFQ:length_z for each fiber: [ 1.30492634  0.4455846   0.94686728  0.37397279 -0.55698075 -0.05569808
 -1.41632249 -0.48536894 -0.843428   -0.27053351 -1.70276973  1.23331453
  2.66555075 -0.77181619 -0.48536894 -1.98921698  0.87525547  1.01847909
 -0.48536894  0.87525547  1.30492634  0.30236098 -0.91503981  0.58880823
 -1.34471068  0.51719641  0.66042004  0.66042004  0.23074917  1.01847909
 -1.91760517  0.4455846  -0.70020438 -0.91503981 -0.12730989  0.01591374
 -1.98921698  1.16170272  2.09265626  0.15913736  0.87525547  0.66042004
 -0.41375713 -0.27053351  0.15913736  0.08752555 -1.4879343   0.30236098
  0.73203185  0.30236098 -0.70020438  1.01847909 -0.48536894  0.58880823
  1.37653815 -0.62859257 -1.84599336  0.08752555 -0.91503981 -0.77181619
  0.73203185 -1.20148706 -0.12730989]
DEBUG:AFQ:Rounds elapsed: 10, num removed: 1
DEBUG:AFQ:Removed indicies: [32]
DEBUG:AFQ:Shape of fgarray: (62, 100, 

DEBUG:AFQ:Removed indicies: [38 42 51]
DEBUG:AFQ:Shape of fgarray: (55, 100, 3)
DEBUG:AFQ:Shape of m_dist: (55, 100)
DEBUG:AFQ:Maximum m_dist: 3.4718433228138674
DEBUG:AFQ:Maximum m_dist for each fiber: [2.88051825 1.47450499 2.50019755 1.8903027  1.80232001 1.9490186
 2.01574993 2.0854105  1.62961757 1.492643   3.47184332 2.64017727
 2.92869667 1.47917445 2.78657327 2.70641735 1.66221683 2.3903874
 1.77317794 1.84493077 3.02084667 2.48860707 2.1284954  2.35240922
 1.63036444 1.94914389 2.46850188 2.18244491 1.85314208 1.29211336
 3.26786632 1.74804005 2.15295112 2.12803797 2.78613043 2.29719381
 2.02862107 2.30328904 1.70772504 2.80571022 1.87139037 2.12442982
 2.51843708 2.98056813 2.33049289 1.62956875 1.73148779 2.54036363
 1.63864885 1.93738947 2.37458394 2.30908582 2.09580426 1.58942552
 1.65700505]
DEBUG:AFQ:Shape of length_z: (55,)
DEBUG:AFQ:Maximum length_z: 2.668956346179147
DEBUG:AFQ:length_z for each fiber: [ 1.23055543  0.32209169  0.85202887  0.24638638 -0.73778267 -0.207

DEBUG:AFQ:Shape of length_z: (86,)
DEBUG:AFQ:Maximum length_z: 4.50996511302891
DEBUG:AFQ:length_z for each fiber: [-0.78911219  0.09735056 -0.53302295 -0.82851053  1.61418681  3.17042141
  0.78682158 -0.65121798 -0.51332378 -0.29663288  0.05795222  1.49599178
 -0.63151881 -0.74971384 -0.73001467 -0.13903951 -0.92700639 -0.76941301
 -0.15873868 -0.19813702 -0.39512874 -0.90730722 -0.43452709  0.94441496
  0.21554559 -0.13903951 -0.07994199  0.3534398  -0.4936246  -0.69061632
 -0.86790887 -0.43452709 -0.17843785 -0.88760805 -0.07994199 -0.86790887
 -0.63151881  4.50996511 -0.80881136 -0.51332378  0.78682158 -0.04054364
  0.07765139  0.53073235  0.45193566 -0.53302295 -0.80881136 -0.55272212
  0.80652076  0.60952903  2.22486115  1.77178019 -0.73001467  0.09735056
 -0.88760805  0.21554559 -0.41482792  2.36275535 -0.61181964  1.25960171
  0.62922821 -0.4936246  -0.31633205  1.43689426 -0.3557304  -0.55272212
 -0.82851053 -0.25723454  1.5550893   0.57013069 -0.80881136  1.49599178
  1.67328

DEBUG:AFQ:Shape of length_z: (62,)
DEBUG:AFQ:Maximum length_z: 4.067832475622998
DEBUG:AFQ:length_z for each fiber: [-0.85679698  0.9596647   4.06783248 -0.57423627 -0.29167557  0.1523484
  0.87893307 -0.53387046 -0.77606535 -0.73569954  0.47527492 -1.13935769
 -0.81643117  0.43490911  0.35417748 -0.04948068 -0.13021231  2.69539476
  1.2018596   0.47527492  0.59637237 -0.25130975 -0.65496791 -1.01826024
  0.39454329 -1.05862606  0.59637237 -1.01826024 -0.53387046 -0.8971628
 -0.29167557  2.37246824  0.677104    0.91929889  1.84771264  1.68624938
 -0.33204138 -0.8971628  -0.3724072   0.9596647  -1.05862606 -0.08984649
 -0.49350464  0.11198258  0.03125095 -0.3724072  -0.93752861  0.23308003
 -0.8971628  -0.00911486 -1.13935769 -0.8971628   0.03125095  0.27344585
 -0.61460209 -0.77606535 -0.21094394  0.31381166  0.23308003 -0.17057812
 -1.05862606 -1.01826024]
DEBUG:AFQ:Rounds elapsed: 4, num removed: 2
DEBUG:AFQ:Removed indicies: [31 54]
DEBUG:AFQ:Shape of fgarray: (60, 100, 3)
DEBUG:AFQ

DEBUG:AFQ:Maximum length_z: 3.5276616304169663
DEBUG:AFQ:length_z for each fiber: [-0.76995501  1.42768986 -0.42809914 -0.08624327  1.33001676 -0.67228191
 -0.62344535 -1.11181088 -0.72111846  0.79281468  0.20677604  0.10910294
  3.52766163 -0.03740672 -0.96530122  0.74397812 -1.01413778  0.98816089
 -0.96530122 -0.37926259 -0.81879157 -0.08624327  1.08583399  2.50209402
  2.30674781 -0.13507983 -0.81879157 -0.18391638 -1.01413778  0.15793949
 -0.33042604  0.40212225  0.30444915 -0.18391638 -0.86762812  0.54863191
 -0.81879157  0.2556126  -1.11181088 -0.81879157  0.30444915 -0.67228191
  0.01142983  0.54863191  0.06026638 -1.01413778 -0.96530122]
INFO:AFQ:Saving /Users/john/AFQ_data/stanford_hardi_vof/derivatives/afq/sub-01/ses-01/sub-01_ses-01_dwi_space-RASMM_model-probCSD_algo-AFQ_desc-clean_tractography.trk
INFO:AFQ:Saving /Users/john/AFQ_data/stanford_hardi_vof/derivatives/afq/sub-01/ses-01/sub-01_ses-01_dwi_space-RASMM_model-probCSD_algo-AFQ_desc-profiles_dwi.csv
INFO:AFQ:Loading 

In [17]:
myafq.export_all()

INFO:AFQ:Saving /Users/john/AFQ_data/stanford_hardi_vof/derivatives/afq/sub-01/ses-01/clean_bundles/sub-01_ses-01_dwi_space-RASMM_model-probCSD_algo-AFQ_desc-ARCL_tractography.trk
INFO:AFQ:Saving /Users/john/AFQ_data/stanford_hardi_vof/derivatives/afq/sub-01/ses-01/clean_bundles/sub-01_ses-01_dwi_space-RASMM_model-probCSD_algo-AFQ_desc-ARCR_tractography.trk
INFO:AFQ:Saving /Users/john/AFQ_data/stanford_hardi_vof/derivatives/afq/sub-01/ses-01/clean_bundles/sub-01_ses-01_dwi_space-RASMM_model-probCSD_algo-AFQ_desc-LpArc_tractography.trk
INFO:AFQ:Saving /Users/john/AFQ_data/stanford_hardi_vof/derivatives/afq/sub-01/ses-01/clean_bundles/sub-01_ses-01_dwi_space-RASMM_model-probCSD_algo-AFQ_desc-RpArc_tractography.trk
INFO:AFQ:Saving /Users/john/AFQ_data/stanford_hardi_vof/derivatives/afq/sub-01/ses-01/clean_bundles/sub-01_ses-01_dwi_space-RASMM_model-probCSD_algo-AFQ_desc-Lvertical_tractography.trk
INFO:AFQ:Saving /Users/john/AFQ_data/stanford_hardi_vof/derivatives/afq/sub-01/ses-01/clean_b